#preamble

In [ ]:
# Choose python version (3.8.16 should be fine normally)
# https://www.datasciencelearner.com/change-python-version-in-google-colab-steps/
!python --version
#!sudo update-alternatives --install /usr/bin/python3 python3 /usr/bin/python3.8 1
#!sudo update-alternatives --config python3
#!python3 --version
#!sudo apt install python3-pip

Python 3.10.12


In [ ]:
%%capture
!pip install git+https://github.com/huggingface/transformers.git
#!pip install transformers==4.7.0
!pip install tokenizers==0.10.3

In [ ]:
import torch
import transformers
from transformers import GPT2Tokenizer, GPT2LMHeadModel
import numpy as np

In [ ]:
! nvidia-smi

Sun Jun 25 23:38:38 2023       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 525.85.12    Driver Version: 525.85.12    CUDA Version: 12.0     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|                               |                      |               MIG M. |
|===============================+======================+======================|
|   0  Tesla T4            Off  | 00000000:00:04.0 Off |                    0 |
| N/A   43C    P8     9W /  70W |      0MiB / 15360MiB |      0%      Default |
|                               |                      |                  N/A |
+-------------------------------+----------------------+----------------------+
                                                                               
+-------

In [ ]:
# Check GPU is available and libraries version
print('Pytorch version ...............{}'.format(torch.__version__))
print('Transformers version ..........{}'.format(transformers.__version__))
print('GPU available .................{}'.format('\u2705' if torch.cuda.device_count() > 0 else '\u274c'))
print('Available devices .............{}'.format(torch.cuda.device_count()))
print('Active CUDA Device: ...........{}'.format(torch.cuda.current_device()))
print('Current cuda device: ..........{}'.format(torch.cuda.current_device()))

Pytorch version ...............2.0.1+cu118
Transformers version ..........4.31.0.dev0
GPU available .................✅
Available devices .............1
Active CUDA Device: ...........0
Current cuda device: ..........0


# Load the pre-trained model and the tokenizer

In [ ]:
# Query GPU memory used before loading the model.
if torch.cuda.is_available():
  device = torch.device('cuda:0')
else:
  device = torch.device('cpu')
#memory_used_s = !nvidia-smi --query-gpu=memory.used --format=csv | grep ' MiB'
#memory_used_s = int(memory_used_s[0][:-4])

In [ ]:
# Load pretrained model and tokenizer.
# The model will be downloaded from HuggingFace hub and cached.
# It may take ~5 minutes for the first excecution.

model = GPT2LMHeadModel.from_pretrained("asi/gpt-fr-cased-small").to(device)
tokenizer = GPT2Tokenizer.from_pretrained("asi/gpt-fr-cased-small")
tokenizer.add_special_tokens({
  "eos_token": "</s>",
  "bos_token": "<s>",
  "unk_token": "<unk>",
  "pad_token": "<pad>",
  "mask_token": "<mask>"
})

0

In [ ]:
# Query GPU memory used after loading the model.
#memory_used_e = !nvidia-smi --query-gpu=memory.used --format=csv | grep ' MiB'
#memory_used_e = int(memory_used_e[0][:-4])
#print("Model loaded in GPU memory and uses {:.2f} Go GPU RAM.".format(float(memory_used_e - memory_used_s)/1024))

In [ ]:
# Check number of parameters.
print("Model has {:,} parameters.".format(model.num_parameters()))

Model has 124,242,432 parameters.


In [ ]:
input_sentence = "Longtemps je me suis couché de bonne heure. \n Un jour je veux"
input_ids = tokenizer.encode(input_sentence, return_tensors='pt').to(device)

print(input_ids[0].size())
s = tokenizer.convert_ids_to_tokens(input_ids[0])
print(s) # a list of tokens
print("decode: ", tokenizer.decode(input_ids[0]))

print("line break")
line_break = tokenizer.encode("ĠĊ", return_tensors='pt')
print(line_break)
print(tokenizer.decode(line_break[0]))

outputs = model(input_ids) # an object of CausalLMOutputWithCrossAttentions
print(type(outputs))
print(outputs.logits.size()) # (batch_size, sequence_length, config.vocab_size)
print('loss', outputs.loss)

next_token_logits = outputs.logits[:, -1, :] # logit of the first token after the input sentence is situated in the last word of the sequence
print(next_token_logits.size())

#print(tokenizer.convert_ids_to_tokens(outputs.logits))

next_token_proba = torch.nn.functional.softmax(next_token_logits, dim=-1) # A dimension along which Softmax will be computed (so every slice along dim will sum to 1)
print(next_token_proba.size())

next_token_log_proba = torch.nn.functional.log_softmax(next_token_logits, dim=-1)
top10 = torch.topk(next_token_log_proba, k=10, dim=-1)
top10_log_proba = top10.values
top10_indices = top10.indices
print('top10 log proba:', top10_log_proba)
print('top10 indices:', top10_indices)
print(tokenizer.convert_ids_to_tokens(top10_indices[0]))

beam_outputs = model.generate(
    input_ids,
    max_length=50,
    do_sample=True,
    top_k=50,
    top_p=0.95,
    num_return_sequences=5
)

print("Output:\n" + 100 * '-')

print(beam_outputs.size())

tokenizer.decode(beam_outputs[0], skip_special_tokens=False)
#tokenizer.convert_ids_to_tokens(beam_outputs[0], skip_special_tokens=False)


torch.Size([15])
['Long', 'temps', 'Ġje', 'Ġme', 'Ġsuis', 'ĠcouchÃ©', 'Ġde', 'Ġbonne', 'Ġheure', '.', 'ĠĊ', 'ĠUn', 'Ġjour', 'Ġje', 'Ġveux']
decode:  Longtemps je me suis couché de bonne heure. 
 Un jour je veux
line break
tensor([[128, 205, 128, 183]])
ĠĊ
<class 'transformers.modeling_outputs.CausalLMOutputWithCrossAttentions'>
torch.Size([1, 15, 50000])
loss None
torch.Size([1, 50000])
torch.Size([1, 50000])
top10 log proba: tensor([[-3.0178, -3.0214, -3.1387, -3.2197, -3.2805, -3.3214, -3.3772, -3.4249,
         -3.4306, -3.7099]], device='cuda:0', grad_fn=<TopkBackward0>)
top10 indices: tensor([[ 501,  638,  660,  301,  478,  249, 2082,  608, 1849,  226]],
       device='cuda:0')
['Ġme', 'ĠÃªtre', 'Ġdire', 'Ġque', 'Ġte', 'Ġun', 'Ġaller', 'Ġfaire', 'Ġsavoir', 'Ġm']
Output:
----------------------------------------------------------------------------------------------------
torch.Size([5, 50])


"Longtemps je me suis couché de bonne heure. \n Un jour je veux voir des yeux clairs. Quand j'ai senti que je devais mourir, j'ai réalisé que j'avais fait mon devoir. Ce n'est que dans le temps"

#Data preparation

## ->Prepare training corpus (CFPP)

In [ ]:
from collections import defaultdict
import re

path = "/content/drive/MyDrive/gpt2_train/CFPP_corpus/"
filename = "CFPP_v1_text.txt"
#filename = "CFPP_v2_text_concat_adjacent_turns.txt"

def parse_line(line):
    '''get for each line interval, sent_id, speaker, sent'''
    # the second ":" from left to right is the delimeter for speakers, the first ":" is the delimeter for startpoint and endpoint of an interval
    # line = 2.242:2.552 (2) André: ah
    #print(line)
    head1, head2, sent = line.split(":", 2)
    head = head1 + ":" + head2
    sent = sent.strip()

    head, speaker = head.split(") ")
    speaker = speaker.strip()
    interval, sent_id = head.split(" (")
    interval = interval.strip()
    sent_id = sent_id

    return interval, sent_id, speaker, sent

def clean_symbols(sent):
    '''clean symbols in the transcription, but keep (1) and (2) for overlapping for later'''
    # replace parenthesis and their content, except for (1) and (2) marking overlapping
    sent = re.sub(r" ?\([^12]+?\)", "", sent)
    # +: indicates pause, replace them by blank, given that , is not present and + is not added systematically
    sent = re.sub(r"\++", "", sent)
    # //: indicates long pause
    sent = re.sub(r"//+", "", sent)
    # r"/.+,.+/": indicates variation of transcription, or guess in case of ununderstandable sequences
    # remove / and ,
    sent = re.sub(r"[/,]", "", sent)
    # delete extra space
    sent = re.sub(r" ( )+", " ", sent)
    #print(sent)

    return sent



### split overlap turns

In [ ]:
def process_corpus_txt_split_overlap(path, filename):
    '''for file: CFPP_v1_text.txt
    output: dataset = {doc: [(interval, sent_id, speaker, sent), ...]}
    {doc: ["spk: content", "spk: content"]}'''
    docs = [doc for doc in open(path+filename).read().split("\n\n") if doc]

    dataset = {}

    for doc in docs:
        doc_name = ""
        lines = [line.strip() for line in doc.split("\n") if line]

        for line in lines:
            if re.match("#", line):
                doc_name = line.split("=")[1].strip()
                dataset[doc_name] = []
            else:
                ## get for each line interval, sent_id, speaker, sent
                interval, sent_id, speaker, sent = parse_line(line)

                ## symbols in the transcription
                # replace parenthesis and their content, except for (1) and (2) marking overlapping
                sent = clean_symbols(sent)

                if "(1)" in sent: # overlapping
                    sents= [sent.strip() for sent in sent.split("(")]

                    if len(speaker.split(" ")) == 2:
                        spk1, spk2 = speaker.split(" ")
                    elif len(speaker.split(" ")) == 1: # if spk2 is missing while (2) is in the sentence, attribute spk1 to the sent
                        spk1 = speaker
                        spk2 = speaker
                    else:
                        print("speaker problem", speaker)
                    for sent in sents:
                        if sent:
                            if sent.startswith("1)") and len(sent)>2:
                                dataset[doc_name].append((interval, sent_id, spk1.strip(), sent[2:].strip()))
                            elif sent.startswith("2)") and len(sent)>2:
                                dataset[doc_name].append((interval, sent_id, spk2.strip(), sent[2:].strip()))
                            else: # ignore other cases due to mistakes of transcription
                                pass #print(speaker, line, '--', sent)
                else: # no overlaping
                    dataset[doc_name].append((interval, sent_id, speaker, sent))

    return dataset

### keep turns as they were in the txt file

In [ ]:
def process_corpus_txt_as_they_were(path, filename):
    '''output: dataset = {doc: ["spk: content", "spk: content"]}
    append sent regardless of whether turns are overlapping
    keep the way they are'''
    docs = [doc for doc in open(path+filename).read().split("\n\n") if doc]

    dataset = {}

    for doc in docs:
        doc_name = ""
        lines = [line.strip() for line in doc.split("\n") if line]

        for line in lines:
            if re.match("#", line):
                doc_name = line.split("=")[1].strip()
                dataset[doc_name] = []
            else:
                #print(line)
                ## get for each line interval, sent_id, speaker, sent
                interval, sent_id, speaker, sent = parse_line(line)

                ## symbols in the transcription
                # replace parenthesis and their content, except for (1) and (2) marking overlapping
                sent = clean_symbols(sent)

                dataset[doc_name].append((interval, sent_id, speaker, sent))

    return dataset

### process txt to dataset

In [ ]:
import json
def save2json(data, outputname):
    json_str = json.dumps(data, indent=4)
    with open(outputname + '.json', 'w') as json_file:
        json_file.write(json_str)

#filename = "CFPP_v1_text.txt"
path = "/content/drive/MyDrive/gpt2_train/CFPP_corpus/"

## convert the corpus into dataset
# split overlap turns into severals
dataset = process_corpus_txt_split_overlap(path, filename)
# keep turns as they were in the txt file
#dataset = process_corpus_txt_as_they_were(path, filename)

# test
for doc in dataset:   # dataset: k: doc_name, v: a list of tuples, where elements represent respectively interval, sent_id, speaker and sentence
    print(doc, dataset[doc][0:8])

## save to json
#save2json(dataset, path+'CFPP_corpus_by_doc')

## load json
#filename = 'CFPP_corpus_by_doc.json'
#dataset = json.load(open(path+filename, encoding='utf-8'))

Andre_Morange_H_58_Mo-v2 [('0:2.242', '1', 'Sonia', "voilà je crois que c'est bon"), ('2.242:2.552', '2', 'André', 'ah'), ('2.552:4.698', '3', 'Sonia', "cette fois c'est réglé"), ('4.698:6.372', '4', 'André', 'pas de test à faire particuliè- particulier'), ('6.372:11.285', '5', 'Sonia', 'oui euh on va juste vérifier que votre voix passe aussi bien que la mienne'), ('11.285:14.557', '6', 'André', "d'accord donc euh je suis André Morange c'est bon"), ('14.557:15.038', '7', 'Sonia', "c'est parfait"), ('15.038:18.524', '8', 'André', 'allons-y alors et bien écoutez allons-y je vous écoute alors')]
Anita_MUSSO_F_46_11e-v2 [('0:31.210', '954', 'Anita', "bon je reviens sur cette euh ce problème qui est un problème euh voilà de d'être chez moi combien de fois ça m'est arrivé bon ben là tu vas boulevard Voltaire c'est pas loin euh tu tu j'y vais à pieds je suis chez moi je me conditionne dans mon appartement en me disant j'y vais à pieds moi ma voiture elle est garée dans la rue j'ai un stationn

### -> convert dataset into a list of lists, where each list represents all sentences of an interview

In [ ]:
def convert_dataset_to_lists_sents(dataset, add_speaker, add_line_break, capitalize_first_token):
    '''input: dataset = {doc: [intervals, sent_ids, speakers, sents] }
    output (if add_speaker == False): docs: [[sent1, sent2, ...], [sent1, sent2, ...]]
    output (if add_speaker == True): docs = [["Spk: Sent1", "Spk: Sent2", ...], ["Spk: Sent1", "Spk: Sent2", ...]]'''
    docs = []
    if add_speaker is False:
        for doc in dataset: # delete intervals, sent_ids, speakers
            docs.append(list(zip(*dataset[doc]))[-1]) #docs: [[sent1, sent2, ...], [sent1, sent2, ...]]
    # add speaker and separate speaker and sent by :
    elif add_speaker is True and add_line_break is True:
        for doc in dataset: # delete intervals, sent_ids, speakers
            intervals, sent_ids, speakers, sents = list(zip(*dataset[doc]))
            assert len(speakers) == len(sents)
            if capitalize_first_token is False:
                newsents = [speakers[i] + ": " + sents[i].strip() + "\n" for i in range(len(sents))]
            else: #capitalize first token
                newsents = [speakers[i] + ": " + sents[i].strip().capitalize() + "\n" for i in range(len(sents))]
            docs.append(newsents) #docs: [["Spk: Sent1", "Spk: Sent2", ...], ["Spk: Sent1", "Spk: Sent2", ...]]
    return docs



#### training examples without speakers

In [ ]:
# suppress speaker from the sent
docs = convert_dataset_to_lists_sents(dataset, add_speaker=False, add_line_break=False, capitalize_first_token=False)
print(len([sent for doc in docs for sent in doc])) # 51479
print(docs[0][:10])

66270
("voilà je crois que c'est bon", 'ah', "cette fois c'est réglé", 'pas de test à faire particuliè- particulier', 'oui euh on va juste vérifier que votre voix passe aussi bien que la mienne', "d'accord donc euh je suis André Morange c'est bon", "c'est parfait", 'allons-y alors et bien écoutez allons-y je vous écoute alors', "oui donc euh je voudrais d'abord savoir comment vous ou vos parents vous étiez arrivés à Montreuil puisque pour moi vous êtes d'abord un", 'oui')


#### training examples with speakers

In [ ]:
# make speaker becomes part of the sent
docs = convert_dataset_to_lists_sents(dataset, add_speaker=True, add_line_break=True, capitalize_first_token=True)
# docs: [["Spk: Sent1", "Spk: Sent2", ...], ["Spk: Sent1", "Spk: Sent2", ...]]
print(len([sent for doc in docs for sent in doc])) # 51479
print(docs[0][:10])

print()
line_break = tokenizer.encode("hi\n", return_tensors='pt')
print(line_break)
print(tokenizer.convert_ids_to_tokens(line_break[0]))

66270
["Sonia: Voilà je crois que c'est bon\n", 'André: Ah\n', "Sonia: Cette fois c'est réglé\n", 'André: Pas de test à faire particuliè- particulier\n', 'Sonia: Oui euh on va juste vérifier que votre voix passe aussi bien que la mienne\n', "André: D'accord donc euh je suis andré morange c'est bon\n", "Sonia: C'est parfait\n", 'André: Allons-y alors et bien écoutez allons-y je vous écoute alors\n', "Sonia: Oui donc euh je voudrais d'abord savoir comment vous ou vos parents vous étiez arrivés à montreuil puisque pour moi vous êtes d'abord un\n", 'André: Oui\n']

tensor([[3671,  171]])
['hi', 'Ċ']


### ->Batch generator

In [ ]:
class BatchGenerator:
    '''
    prepare_examples: concatenate tokens into doc in the limite of max_length (without confounding document boundaries), then encode the concatenated sequence (example) with truncation and padding
    get_a_random_batch: select examples by random indexes, then return a batch (by _ids_to_batch)
    '''
    def __init__(self, docs, tokenizer, max_length):

        self.docs = docs
        self.tokenizer = tokenizer

        self.string_examples = []
        self.encoded_examples = [] # list of tensors of shape [0, 1024]
        self.prepare_examples(max_length)

    def prepare_examples(self, max_length):

        # concatenate tokens into doc in the limite of max_length (without confounding document boundaries)
        docs_examples_tokens = []

        for doc in self.docs:
            doc_example_tokens = ""
            doc_example_ids = []
            for sent in doc:
                if len(doc_example_tokens.split(" ")) < max_length:
                    if doc_example_tokens == "":
                        doc_example_tokens = sent
                    else:
                        doc_example_tokens += " " + sent
                else: # exceed maximun length
                    docs_examples_tokens.append(doc_example_tokens)
                    self.string_examples.append(doc_example_tokens)
                    doc_example_tokens = sent

            #some examples may contain less than 1024 tokens, because the last example of a doc may not be enough long
            docs_examples_tokens.append(doc_example_tokens)
            self.string_examples.append(doc_example_tokens)

        # encode the concatenated sequence (example) with truncation and padding
        for exa in docs_examples_tokens:
            exa_ids = self.tokenizer.encode(exa, add_special_tokens=True,
                                            padding='max_length',
                                            truncation=True,
                                            is_split_into_words=True,
                                            max_length=max_length,
                                            return_tensors='pt',
                                            add_prefix_space=False)
            self.encoded_examples.append(exa_ids)
            # only consider examples which have more than max_length subtokens, and cut last sentence of the batch if it exceeds maximal length (1024 here)
            #if exa_ids.size(dim=1) >= max_length:
            #    self.encoded_examples.append(exa_ids[:, :max_length])


    # Returns a random training batch (composed of pairs of consecutive paragraphs).
    # If `subset` is an integer, only a subset of the corpus is used. This can be useful to debug the system.
    def get_a_random_batch(self, batch_size, subset=None):
        # select examples by random indexes
        max_i = self.length() if(subset is None) else min(subset, self.length())
        example_ids = np.random.randint(max_i, size=batch_size) # Randomly picks some example ids.
        #print(example_ids)

        return self._ids_to_batch(example_ids)

    # Convert example ids into real batch, and turn it into a tensor
    def _ids_to_batch(self, example_ids):
        # turn indexes into a batch
        batch = [self.encoded_examples[exa] for exa in example_ids]

        return torch.cat([b for b in batch], dim=0)


    def length(self):
        return len(self.encoded_examples)

    def convert_batch_ids_to_tokens(self, input_batch):
        print('input batch size:', input_batch.size(dim=0))
        for i in range(input_batch.size(dim=0)):
            print('example', i)
            print('convert ids to tokens function:', self.tokenizer.convert_ids_to_tokens(input_batch[i]))
            print('decode function:', self.tokenizer.decode(input_batch[i]))


    # Returns a generator of training batches for a full epoch.
    # If `subset` is an integer, only a subset of the corpus is used. This can be useful to debug the system.
    # (not used in current training)
    def all_batches(self, batch_size, subset=None):
        max_i = self.length() if(subset is None) else min(subset, self.length())
        #example_ids = np.random.randint(max_i, size=batch_size)

        # Loop that generates all full batches (batches of size 'batch_size')
        i = 0
        while((i + batch_size) <= max_i):
            instance_ids = np.arange(i, (i + batch_size))
            yield self._ids_to_batch(instance_ids)
            i += batch_size

        # Possibly generates the last (not full) batch.
        if(i < max_i):
            instance_ids = np.arange(i, max_i)
            yield self._ids_to_batch(instance_ids)

    '''
    def prepare_docs(self):
        docs_sents_tokens = []
        docs_sents_ids = []

        for doc in self.docs:
            doc_sents_tokens = []
            doc_sents_ids = []
            for sent in doc:
                doc_sents_tokens.append(sent)
                doc_sents_ids.append(self.tokenizer.encode(sent, return_tensors='pt'))

            docs_sents_tokens.append(doc_sents_tokens)
            docs_sents_ids.append(doc_sents_ids)

        return docs_sents_tokens, docs_sents_ids


    def get_examples(self, max_length):
        docs_sents_tokens, docs_sents_ids = self.prepare_docs()
        print(len(docs_sents_tokens[0]))
        assert len(docs_sents_tokens) == len(docs_sents_ids)

        for encoded_doc in docs_sents_ids:
            leng = 0
            begin_i = 0
            for i, sent_ids in enumerate(encoded_doc):
                if leng < max_length:
                    #print(sent_ids.size())
                    leng += sent_ids.size(dim=1)
                else:
                    self.examples_ids.append(torch.cat((encoded_doc[begin_i:i]), dim=1)[:, :max_length])
                    begin_i = i
                    leng = 0
    '''



test batch

In [ ]:
rand_batch = BatchGenerator(docs, tokenizer=tokenizer, max_length=1024).get_a_random_batch(2, subset=10)
print(rand_batch.size())
print(rand_batch)

BatchGenerator(docs, tokenizer=tokenizer, max_length=1024).convert_batch_ids_to_tokens(rand_batch)

#l = BatchGenerator(docs, tokenizer=tokenizer, max_length=1024).length()
#print('number of all batches:', l) #680


torch.Size([2, 1024])
tensor([[8006,  599, 2562,  ..., 3764,  262, 2095],
        [9799,  322, 1593,  ...,  528,  219,  249]])
input batch size: 2
example 0
convert ids to tokens function: ['oui', 'Ġbien', 'ĠsÃ»r', 'Ġc', "'", 'est', 'Ġune', 'Ġri', '-', 'Ġune', 'Ġpartie', 'Ġde', 'Ġmon', 'ĠidentitÃ©', 'Ġqui', 'Ġqui', 'Ġest', 'Ġdisparue', 'Ġc', "'", 'est', 'Ġcertain', 'Ġmais', 'Ġpetit', 'Ġvous', 'Ġvous', 'Ġsenti', 'ez', 'Ġpas', 'ĠparticuliÃ¨rement', 'Ġportugais', 'Ġoh', 'Ġpas', 'Ġdu', 'Ġtout', 'Ġdu', 'Ġtout', 'Ġ-', 'Ġvous', 'Ġn', "'", 'Ã©tiez', 'Ġpas', 'Ġen', 'Ġtrain', 'Ġde', 'Ġle', 'Ġrevendiquer', 'Ġah', 'Ġnon', 'Ġnon', 'Ġnon', 'Ġalors', 'Ġabsolument', 'Ġpas', 'Ġnon', 'Ġc', "'", 'Ã©tait', 'Ġces', 'ĠidentitÃ©s', 'ĠÃł', 'Ġl', "'", 'Ã©cole', 'Ġc', "'", 'Ã©tait', 'Ġun', 'ĠproblÃ¨me', 'ĠÃ§a', 'Ġsortait', 'Ġeuh', 'Ġpour', 'Ġles', 'ĠArabes', 'Ġon', 'Ġdisait', 'Ġl', "'", 'Ara', 'be', 'Ġle', 'ĠB', 'eur', 'ĠdÃ©jÃł', 'Ġah', 'Ġnon', 'Ġle', 'ĠB', 'eur', 'Ġc', "'", 'Ã©tait', 'Ġnon', 'Ġle', 'ĠB', 'eur'

### ->Split docs into train and test
no reverse order, so we always have the same test set

#### ->function

In [ ]:
# reserver une portion pour l'evaluation
def train_test_split(docs, test_portion):
    lengths = len(docs)
    print(f"number of docs: {lengths}") # 51
    train = docs[:round(lengths*(1-test_portion))]
    test = docs[round(lengths*(1-test_portion)):]
    return train, test

#### split CFPP into train and test

In [ ]:
train, test = train_test_split(docs, test_portion=0.1)
#print(train)
#print(test)

print(len(train)) # 46
print(len(test)) # 5
# train
train_batch_generator = BatchGenerator(docs=train, tokenizer=tokenizer, max_length=1024)
print("train size: %s" %train_batch_generator.length()) # padding: 659
# test
test_batch_generator = BatchGenerator(docs=test, tokenizer=tokenizer, max_length=512)
print("test size: %s" %test_batch_generator.length()) # padding: 113 #max_length = 512 -> 205 examples

n = 0
for b in test_batch_generator.all_batches(batch_size=2):
    n+=1

print('number of test batches: ', n) #57

number of docs: 51
46
5
train size: 634
test size: 205
number of test batches:  103


## -> Prepare fine-tune corpus (MPF)

In [ ]:
mpf_path = "/content/drive/MyDrive/gpt2_train/MPF_corpus/"
mpf_filename = "MPF_version4b_full_text.txt"

def parse_line(line):
    '''get for each line interval, sent_id, speaker, sent'''
    # the second ":" from left to right is the delimeter for speakers, the first ":" is the delimeter for startpoint and endpoint of an interval
    # line = 0:5 (2) Julie:  Alors (.) est-ce déjà vous pouvez me dire euh chacune votre tour votre prénom (?)
    #print(line)
    head1, head2, sent = line.split(":", 2)
    head = head1 + ":" + head2
    sent = sent.strip()

    head, speaker = head.split(") ")
    speaker = speaker.strip()
    interval, sent_id = head.split(" (")
    interval = interval.strip()
    sent_id = sent_id

    return interval, sent_id, speaker, sent

def clean_symbols_MPF(sent):
    '''clean symbols in the transcription, but keep (1) and (2) for overlapping for later'''
    # replace parenthesis and their content
    sent = re.sub(r" ?\(.*?\)", "", sent)
    # delete < and > representing overlapping, as well as [ and ]
    sent = re.sub(r"[<>\[\]]", "", sent)
    # replace @s, @a and @@s, @@a, @@ and final .
    sent = ' '.join([re.sub(r'@+(s|a)?\.?$', '', w) for w in sent.split(" ")])
    # replace final .
    sent = ' '.join([re.sub(r'\.$', '', w) for w in sent.split(" ")])
    # remove &=
    sent = ' '.join([w for w in sent.split(" ") if not re.match('&=', w)])
    # remove / and ,
    #sent = re.sub(r"[/,]", "", sent)
    # delete extra space
    sent = re.sub(r" ( )*", " ", sent).strip()
    #print(sent)

    return sent


def process_MPF_corpus_text(path, filename):
    '''for file: MPF_version4b_full_text.txt
    output: dataset = {doc: [(interval, sent_id, speaker, sent), ...]}
    {doc: ["spk: content", "spk: content"]}'''
    docs = [doc for doc in open(path+filename).read().split("\n\n") if doc]

    dataset = {}

    for doc in docs:
        doc_name = ""
        lines = [line.strip() for line in doc.split("\n") if line]

        for line in lines:
            if re.match("newdoc id", line):
                doc_name = line.split("=")[1].strip()
                dataset[doc_name] = []
            elif line.strip() != '':
                ## get for each line interval, sent_id, speaker, sent
                # line = 0:5 (2) Julie:  Alors (.) est-ce déjà vous pouvez me dire euh chacune votre tour votre prénom (?)
                interval, sent_id, speaker, sent = parse_line(line)

                #ignore commentaire turn
                if not re.match(r"com", speaker.lower()):
                    ## clean symbols in the transcription
                    sent = clean_symbols_MPF(sent)
                    if sent:
                        #lowercasing initial character
                        sent = sent[0].lower() + sent[1:]
                        dataset[doc_name].append((interval, sent_id, speaker, sent))

    return dataset



### process txt to dataset

In [ ]:
## convert the corpus into dataset
mpf_dataset = process_MPF_corpus_text(mpf_path, mpf_filename)

# test
for doc in mpf_dataset:   # dataset: k: doc_name, v: a list of tuples, where elements represent respectively interval, sent_id, speaker and sentence
    print(doc, mpf_dataset[doc][0:8])

juliet2_anon_110915 [('0:5', '2', 'Julie', 'alors est-ce déjà vous pouvez me dire euh chacune votre tour votre prénom'), ('5:6', '4', 'Kimia', "bien sûr moi c'est kimia"), ('6:7', '6', 'Elikia', "et moi c'est elikia"), ('9:13', '8', 'Julie', "euh est est-ce que tu peux te mettre à côté d'elle s'il te plaît ce sera plus facile pour le micro je suis désolée"), ('14:18', '10', 'Julie', 'euh est est-ce que vous pourriez commencer par me présenter les ce ce projet auquel vous avez participé euh ?'), ('19:21', '12', 'Julie', 'co- comment vous raconteriez ce ce projet ?'), ('23:23', '14', 'Kimia', 'tu v-'), ('23:26', '15', 'Elikia', "ben déjà euh le projet il s'intitule nous sommes un musée")]
aristide2a_anon_150618 [('5:6', '1586', 'Aristide', 'bon très bien'), ('8:12', '1588', 'Aristide', "alors euh daniel aujourd'hui je vais t'interviewer euh"), ('13:22', '1590', 'Aristide', "par rapport au projet qu'on a euh en commun donc euh le projet mle-mpf qui consiste à recueillir des données autour

#### examples without speakers

In [ ]:
# suppress speaker from the sent
docs = convert_dataset_to_lists_sents(dataset, add_speaker=False, add_line_break=False, capitalize_first_token=False)
print(len([sent for doc in docs for sent in doc])) # 71772
print(docs[0][:10])

71766
('alors est-ce déjà vous pouvez me dire euh chacune votre tour votre prénom', "bien sûr moi c'est kimia", "et moi c'est elikia", "euh est est-ce que tu peux te mettre à côté d'elle s'il te plaît ce sera plus facile pour le micro je suis désolée", 'euh est est-ce que vous pourriez commencer par me présenter les ce ce projet auquel vous avez participé euh ?', 'co- comment vous raconteriez ce ce projet ?', 'tu v-', "ben déjà euh le projet il s'intitule nous sommes un musée", "euh c'est un projet qui parle de nous", "du d'un cadre")


In [ ]:
from __future__ import print_function # print to file

with open(path + 'MPF_per_text.txt', 'w') as f:
    print(docs, file=f)

#### examples with speakers

In [ ]:
mpf_docs = convert_dataset_to_lists_sents(mpf_dataset, add_speaker=True, add_line_break=True, capitalize_first_token=True)
print(len([sent for mpf_doc in docs for sent in doc])) # 71772
print(docs[0][:10])

71766
['Julie: Alors est-ce déjà vous pouvez me dire euh chacune votre tour votre prénom\n', "Kimia: Bien sûr moi c'est kimia\n", "Elikia: Et moi c'est elikia\n", "Julie: Euh est est-ce que tu peux te mettre à côté d'elle s'il te plaît ce sera plus facile pour le micro je suis désolée\n", 'Julie: Euh est est-ce que vous pourriez commencer par me présenter les ce ce projet auquel vous avez participé euh ?\n', 'Julie: Co- comment vous raconteriez ce ce projet ?\n', 'Kimia: Tu v-\n', "Elikia: Ben déjà euh le projet il s'intitule nous sommes un musée\n", "Elikia: Euh c'est un projet qui parle de nous\n", "Elikia: Du d'un cadre\n"]


#### Split mpf docs into train and test

In [ ]:
mpf_train, mpf_test = train_test_split(mpf_docs, test_portion=0.2)

print(len(mpf_train))
print(len(mpf_test))

# test
mpf_test_batch_generator = BatchGenerator(docs=mpf_test, tokenizer=tokenizer, max_length=512)
print("test size: %s" %test_batch_generator.length()) # 127 379 # max_length = 512 -> 267 examples

n = 0
for b in mpf_test_batch_generator.all_batches(batch_size=2):
    n+=1

print('number of test batches: ', n) #64 221 190

number of docs: 68
54
14
test size: 267
number of test batches:  134


#Training

In [ ]:
import pandas as pd
import numpy as np
import random
import torch
from torch.utils.data import Dataset, DataLoader
from transformers import GPT2Tokenizer, GPT2LMHeadModel, AdamW, get_linear_schedule_with_warmup
from transformers import get_scheduler
from tqdm import tqdm, trange
import torch.nn.functional as F
import csv
import time

In [ ]:
def train(
    model, tokenizer, device, train_batch_generator, test_batch_generator, train_batch_size=5, subset=None,
    epochs=5, lr=2e-5, warmup_steps=10, output_dir=".", output_prefix="wreckgar",
    test_mode=False, save_model_on_epoch=False,
):
    # Create a DataLoader for your training and test datasets so you can iterate over batches of data
    #train_dataloader = DataLoader(train, batch_size=train_batch_size, shuffle=True)

    model.to(device)

    # Create an optimizer and learning rate scheduler to fine-tune the model.
    optimizer = AdamW(model.parameters(), lr=lr)

    if subset:
        epoch_size = round(min(subset, train_batch_generator.length())/train_batch_size)
    else:
        epoch_size = round(train_batch_generator.length()/train_batch_size)

    num_training_steps = epochs * epoch_size

    # Create the default learning rate scheduler from Trainer:
    lr_scheduler = get_scheduler(
    name="linear", optimizer=optimizer, num_warmup_steps=warmup_steps, num_training_steps=num_training_steps
    )

    # use the tqdm library to add a progress bar over the number of training steps
    progress_bar = tqdm(range(num_training_steps))

    model.train() # Tells Pytorch we are in training mode (can be useful if dropout is used, for instance).
    #model.zero_grad() # Makes sure the gradient is reinitialised to zero.

    loss = 0

    time_0 = time.time()

    for epoch in range(epochs):
        instances_processed = 0 # Number of instances trained on in the current epoch
        epoch_loss = []
        print(f"loss before training epoch {epoch}: {loss}")
        print(f"Training epoch {epoch}")

        #print(batch.size())
        while instances_processed <= epoch_size:
            batch = train_batch_generator.get_a_random_batch(train_batch_size, subset=subset).to(device)

            model.zero_grad()
            outputs = model(batch, labels=batch)
            loss = outputs.loss
            #print(outputs.logits.size())
            #print('outputs', outputs)
            #print('loss:', loss)

            epoch_loss.append(loss)

            loss.backward()
            optimizer.step()
            lr_scheduler.step()
            optimizer.zero_grad()
            progress_bar.update(train_batch_size)

            instances_processed += train_batch_size


        # end of epoch
        print(f"-- END OF EPOCH {epoch}.")
        print(f"Losses of epoch {epoch}: {epoch_loss}")

        print(f"Average loss: {sum(epoch_loss) / len(epoch_loss)}.")
        duration = time.time() - time_0
        print(f"{duration} s elapsed (i.e. {duration / (epoch + 1)} s/epoch)")


        # loss in the test
        print("Loss in the test dataset")
        test_loss = []
        with torch.no_grad():
            for batch in test_batch_generator.all_batches(batch_size = 2): #test ex n=97
                batch = batch.to(device)
                loss = model(batch, labels=batch).loss
                test_loss.append(loss)

        print(f"Average test loss: {sum(test_loss) / len(test_loss)}.")

        # Example of generation
        print("-----Generation-----")
        #batch = train_batch_generator.get_a_random_batch(batch_size=1, subset=subset)

        #print(batch[0].size())
        #print(tokenizer.decode(batch[0], skip_special_tokens=True))

        #print("Generation of text in the training set: ")

        #generate(model,tokenizer,device,batch,encoded=True, max_length=50, top_k = 50, top_p = 0.95)

        input_sentence = "La daronne elle était euh marrante et alors ?"
        print("Generation of text of the defined input sentence: ")
        generate(model, tokenizer, device, input_sentence, encoded=False, max_length=50, top_k = 50, top_p = 0.95)
        print()


    return model


In [ ]:
def generate(model, tokenizer, device, input, encoded=False, max_length=100, top_k = 50, top_p = 0.95
):

    if not encoded:
        input = tokenizer.encode(input, return_tensors='pt').to(device)

    beam_outputs = model.generate(
            input.to(device),
            max_length=max_length,
            do_sample=True,
            top_k=top_k,
            top_p=top_p,
            num_return_sequences=1
        )

    print("Output:\n" + 100 * '-')

    print(tokenizer.decode(beam_outputs[0], skip_special_tokens=False))

In [ ]:
model_spk_line_break = train(model, tokenizer, device, train_batch_generator, test_batch_generator, train_batch_size=2, subset=None, epochs=30)

  0%|          | 0/9120 [00:00<?, ?it/s]

loss before training epoch 0: 0
Training epoch 0


  3%|▎         | 306/9120 [01:45<50:22,  2.92it/s]

-- END OF EPOCH 0.
Losses of epoch 0: [tensor(4.7775, device='cuda:0', grad_fn=<NllLossBackward0>), tensor(5.2856, device='cuda:0', grad_fn=<NllLossBackward0>), tensor(4.2656, device='cuda:0', grad_fn=<NllLossBackward0>), tensor(4.6351, device='cuda:0', grad_fn=<NllLossBackward0>), tensor(4.5799, device='cuda:0', grad_fn=<NllLossBackward0>), tensor(4.6477, device='cuda:0', grad_fn=<NllLossBackward0>), tensor(4.6488, device='cuda:0', grad_fn=<NllLossBackward0>), tensor(4.5868, device='cuda:0', grad_fn=<NllLossBackward0>), tensor(4.7202, device='cuda:0', grad_fn=<NllLossBackward0>), tensor(4.3764, device='cuda:0', grad_fn=<NllLossBackward0>), tensor(4.2799, device='cuda:0', grad_fn=<NllLossBackward0>), tensor(4.3546, device='cuda:0', grad_fn=<NllLossBackward0>), tensor(4.1308, device='cuda:0', grad_fn=<NllLossBackward0>), tensor(4.4315, device='cuda:0', grad_fn=<NllLossBackward0>), tensor(4.4560, device='cuda:0', grad_fn=<NllLossBackward0>), tensor(4.4399, device='cuda:0', grad_fn=<NllLo

  7%|▋         | 612/9120 [03:43<48:48,  2.91it/s]

...

-- END OF EPOCH 28.
Losses of epoch 28: [tensor(2.1824, device='cuda:0', grad_fn=<NllLossBackward0>), tensor(2.1042, device='cuda:0', grad_fn=<NllLossBackward0>), tensor(1.3029, device='cuda:0', grad_fn=<NllLossBackward0>), tensor(2.3233, device='cuda:0', grad_fn=<NllLossBackward0>), tensor(1.8715, device='cuda:0', grad_fn=<NllLossBackward0>), tensor(1.3921, device='cuda:0', grad_fn=<NllLossBackward0>), tensor(2.2914, device='cuda:0', grad_fn=<NllLossBackward0>), tensor(2.1046, device='cuda:0', grad_fn=<NllLossBackward0>), tensor(2.3777, device='cuda:0', grad_fn=<NllLossBackward0>), tensor(2.1848, device='cuda:0', grad_fn=<NllLossBackward0>), tensor(2.5391, device='cuda:0', grad_fn=<NllLossBackward0>), tensor(2.0601, device='cuda:0', grad_fn=<NllLossBackward0>), tensor(2.3580, device='cuda:0', grad_fn=<NllLossBackward0>), tensor(2.3012, device='cuda:0', grad_fn=<NllLossBackward0>), tensor(2.0798, device='cuda:0', grad_fn=<NllLossBackward0>), tensor(1.9861, device='cuda:0', grad_fn=<Nll

9180it [58:46,  2.90it/s]

-- END OF EPOCH 29.
Losses of epoch 29: [tensor(2.0796, device='cuda:0', grad_fn=<NllLossBackward0>), tensor(1.5663, device='cuda:0', grad_fn=<NllLossBackward0>), tensor(2.2640, device='cuda:0', grad_fn=<NllLossBackward0>), tensor(2.1034, device='cuda:0', grad_fn=<NllLossBackward0>), tensor(2.3125, device='cuda:0', grad_fn=<NllLossBackward0>), tensor(2.3239, device='cuda:0', grad_fn=<NllLossBackward0>), tensor(2.4100, device='cuda:0', grad_fn=<NllLossBackward0>), tensor(1.2309, device='cuda:0', grad_fn=<NllLossBackward0>), tensor(2.4494, device='cuda:0', grad_fn=<NllLossBackward0>), tensor(2.1987, device='cuda:0', grad_fn=<NllLossBackward0>), tensor(2.1866, device='cuda:0', grad_fn=<NllLossBackward0>), tensor(2.1724, device='cuda:0', grad_fn=<NllLossBackward0>), tensor(2.1488, device='cuda:0', grad_fn=<NllLossBackward0>), tensor(2.5071, device='cuda:0', grad_fn=<NllLossBackward0>), tensor(2.4285, device='cuda:0', grad_fn=<NllLossBackward0>), tensor(2.4417, device='cuda:0', grad_fn=<Nll

9180it [58:59,  2.59it/s]

Output:
----------------------------------------------------------------------------------------------------
La daronne elle était euh marrante et alors? Elle m'a dit que elle était plus sensible a a la politique de la ville elle avait un peu changé donc euh comment tu vas elle s'est fait virer en fait c'est ça



##Save fine-tuned model

In [ ]:
#model_t.save_pretrained(path+'/saved_model_all_train_epoch30/')
#model_spk_line_break.save_pretrained(path+'/saved_model_spk_line_break_epoch30/')

# save tokenizer (only for calculating perplexity)
#tokenizer.save_pretrained(path+'saved_model_all_train_epoch30/')

('/content/drive/MyDrive/gpt2_train/saved_model_all_train_epoch30/tokenizer_config.json',
 '/content/drive/MyDrive/gpt2_train/saved_model_all_train_epoch30/special_tokens_map.json',
 '/content/drive/MyDrive/gpt2_train/saved_model_all_train_epoch30/vocab.json',
 '/content/drive/MyDrive/gpt2_train/saved_model_all_train_epoch30/merges.txt',
 '/content/drive/MyDrive/gpt2_train/saved_model_all_train_epoch30/added_tokens.json')

# Load fine-tuned model

In [ ]:
path = "/content/drive/MyDrive/gpt2_train/"
#model_t = GPT2LMHeadModel.from_pretrained(path+'saved_model_all_train_epoch30/').to(device)
model_t = GPT2LMHeadModel.from_pretrained(path+'/saved_model_spk_line_break_epoch30/').to(device)

#Model evaluation

In [ ]:
input_sentence = "Mon daron"
generate(model_t, tokenizer, device, input_sentence, encoded=False, max_length=50, top_k = 50, top_p = 0.95)

Output:
----------------------------------------------------------------------------------------------------
Mon daron était un personnage assez célèbre dans le quartier et les les gens le choisissaient très souvent parmi les gens qui qui venaient à la gare d'arc-en-ciel ou au kremlin-bicêtre ou qui venaient à la gare


## loss

### validity (pick up a sent from training set)

In [ ]:
with torch.no_grad():
    batch = train_batch_generator.get_a_random_batch(batch_size=1, subset=10).to(device)

    print(batch[0].size())
    print(tokenizer.decode(batch[0], skip_special_tokens=True))

    print("---baseline---")
    outputs = model(batch[0], labels=batch[0])
    loss = outputs.loss
    print("baseline loss:", loss)

    print("---fine-tuned---")
    outputs = model_t(batch[0], labels=batch[0])
    loss = outputs.loss
    print("fine-tuned loss:", loss)

torch.Size([1024])
oui vous avez vous voyez c'est moi j'ai enfin oui Budapest j'ai évolué avec ça je me suis dit il y a eu Budapest quand même il y a eu Prague je veux dire c'est pas possible quoi on peut je veux dire vous voyez et et et il y a quand même un espoir à Cuba donc je me suis écarté de mes pa- de mon père euh ça a été difficile oui c'était difficile parce que c'est c'est quand même il comprenait pas vraiment pour lui c'était un monde qui s'écroule quand même oui une remise en cause trop forte oui trop forte oui ouais quand on milite quelque part et qu'on s'aperçoit que enfin c'est quand même des millions de personnes qui disparaissent quoi on se il y a quand même vous voyez tandis que ma génération à moi a réussi à passer le cap plus facilement en fait parce qu'elle s'est moins impliquée certainement mais en dans soixante-huit vous n'avez pas du tout été touché atteint par alors les ben si parce que j'étais comme tout le monde courant libertaire ben plutôt maoïste mais alor

### self-defined sents

In [ ]:
input_sentence = "Mon père il est là."
input_ids = tokenizer.encode(input_sentence, return_tensors='pt').to(device)
print(input_ids.size())
print(tokenizer.decode(input_ids[0]))
print(tokenizer.convert_ids_to_tokens(input_ids[0]))

# baseline
outputs = model(input_ids, labels=input_ids)
loss = outputs.loss
print(loss)

# fine-tuned
outputs = model_t(input_ids, labels=input_ids)
loss = outputs.loss
print(loss)

In [ ]:
sd1 = "Mon père il est là."
sd2 = "Mon daron il est là"
sd3 = "Ils sont là mes parents"
od1 = "Le gars on l'a appelé"

sd1_ids = tokenizer.encode(sd1, return_tensors='pt').to(device)
sd2_ids = tokenizer.encode(sd2, return_tensors='pt').to(device)
sd3_ids = tokenizer.encode(sd3, return_tensors='pt').to(device)
od1_ids = tokenizer.encode(od1, return_tensors='pt').to(device)

#baseline
'''
model = GPT2LMHeadModel.from_pretrained("asi/gpt-fr-cased-small").to(device)
tokenizer = GPT2Tokenizer.from_pretrained("asi/gpt-fr-cased-small")
tokenizer.add_special_tokens({
  "eos_token": "</s>",
  "bos_token": "<s>",
  "unk_token": "<unk>",
  "pad_token": "<pad>",
  "mask_token": "<mask>"
})
'''

print("---baseline---")
outputs = model(sd1_ids, labels=sd1_ids)
loss = outputs.loss
print("s1", tokenizer.decode(sd1_ids[0]))
print("baseline s1 loss:", loss)

outputs = model(sd2_ids, labels=sd2_ids)
loss = outputs.loss
print("s2", tokenizer.decode(sd2_ids[0]))
print("baseline s2 loss,", loss)

outputs = model(sd3_ids, labels=sd3_ids)
loss = outputs.loss
print("s3", tokenizer.decode(sd3_ids[0]))
print("baseline s3 loss,", loss)

outputs = model(od1_ids, labels=od1_ids)
loss = outputs.loss
print("od", tokenizer.decode(od1_ids[0]))
print("baseline od loss,", loss) #4.36
print()

#fine-tuned model
print("---fine-tuned---")
outputs = model_t(sd1_ids, labels=sd1_ids)
loss = outputs.loss
print("s1", tokenizer.decode(sd1_ids[0]))
print("fine-tuned s1 loss:", loss)

outputs = model_t(sd2_ids, labels=sd2_ids)
loss = outputs.loss
print("s2", tokenizer.decode(sd2_ids[0]))
print("fine-tuned s2 loss,", loss)

outputs = model(sd3_ids, labels=sd3_ids)
loss = outputs.loss
print("s3", tokenizer.decode(sd3_ids[0]))
print("s3 loss,", loss)

outputs = model_t(od1_ids, labels=od1_ids)
loss = outputs.loss
print("od", tokenizer.decode(od1_ids[0]))
print("od loss,", loss) #3.96
print()

---baseline---
s1 Mon père il est là.
baseline s1 loss: tensor(3.6521, device='cuda:0', grad_fn=<NllLossBackward0>)
s2 Mon daron il est là
baseline s2 loss, tensor(5.9396, device='cuda:0', grad_fn=<NllLossBackward0>)
s3 Ils sont là mes parents
baseline s3 loss, tensor(4.6340, device='cuda:0', grad_fn=<NllLossBackward0>)
od Le gars on l'a appelé
baseline od loss, tensor(4.3576, device='cuda:0', grad_fn=<NllLossBackward0>)

---fine-tuned---
s1 Mon père il est là.
fine-tuned s1 loss: tensor(4.4436, device='cuda:0', grad_fn=<NllLossBackward0>)
s2 Mon daron il est là
fine-tuned s2 loss, tensor(3.8522, device='cuda:0', grad_fn=<NllLossBackward0>)
s3 Ils sont là mes parents
s3 loss, tensor(4.6340, device='cuda:0', grad_fn=<NllLossBackward0>)
od Le gars on l'a appelé
od loss, tensor(3.9593, device='cuda:0', grad_fn=<NllLossBackward0>)



###from test set

pick up one batch

In [ ]:
with torch.no_grad():
    batch = test_batch_generator.get_a_random_batch(batch_size=1).to(device)

    print(batch[0].size())
    print(tokenizer.decode(batch[0], skip_special_tokens=True))

    print("---baseline---")
    outputs = model(batch[0], labels=batch[0])
    loss = outputs.loss
    print("baseline loss:", loss)

    print("---fine-tuned---")
    outputs = model_t(batch[0], labels=batch[0])
    loss = outputs.loss
    print("fine-tuned loss:", loss)

torch.Size([1024])
non on parlait normalement à tout va on on rigolait moi moi je je me forçais on déconnait on parlait à parler normalement ouais ouais ouais euh vous n'avez pas d'accent cet espèce d'accent qui chante un peu vous l'avez perdu vous avez non on l'a jamais eu on l'a jamais eu voulu arrêter ou vous l'avez jamais eu on l'a jamais eu moi je l'ai parce que je suis ouais non euh moi j'avais non on l'a jamais eu non non on n'a pas mais sans que ça soit un effort non là on a t- toujours été non moi pour moi j'ai toujours été euh naturel parce que j'ai moi j'ai peut-être dans le ton quand je rigole j'ai un accent parce que des fois il y a des il y a des mots quand on dit euh ouais des fois voilà un peu comme Coluche quand il quand il fait rigoler il a il a toujours un petit accent euh il me semble que vous avez l'accent parisien comme on dit ouais et puis de temps en temps u- une petite trace comme ça de ouais oui c'est vrai vous avez pas tort oui ça c'est vrai que là j' plus l'

the same random batch from test set

In [ ]:
i = 0
baseline_losses = []
fine_tuned_losses = []
with torch.no_grad():
    while i < 10:
        batch = test_batch_generator.get_a_random_batch(batch_size=1, subset=10).to(device)
        #baseline
        outputs = model(batch[0], labels=batch[0])
        loss = outputs.loss
        baseline_losses.append(loss)
        #fine-tuned
        outputs = model_t(batch[0], labels=batch[0])
        loss = outputs.loss
        fine_tuned_losses.append(loss)

        i += 1
        print(i)

print("---baseline---")
print("baseline average loss:", sum(baseline_losses)/len(baseline_losses))

print("---fine-tuned---")
print("fine-tuned loss:", sum(fine_tuned_losses)/len(fine_tuned_losses))

1
2
3
4
5
6
7
8
9
10
---baseline---
baseline average loss: tensor(3.7719, device='cuda:0')
---fine-tuned---
fine-tuned loss: tensor(3.1781, device='cuda:0')


### test set (CFPP)

In [ ]:
baseline_losses = []
fine_losses = []

with torch.no_grad():
    for test_batch in test_batch_generator.all_batches(batch_size = 2): #test ex n=97
        t = test_batch.to(device)
        #baseline
        outputs = model(t, labels=t)
        loss = outputs.loss
        baseline_losses.append(loss)
        #fine-tuned
        outputs = model_t(t, labels=t)
        loss = outputs.loss
        fine_losses.append(loss)

print("---baseline all test set average loss---")
print(sum(baseline_losses)/len(baseline_losses)) #4.15
print(baseline_losses)

print("---fine-tuned all test set average loss---")
print(sum(fine_losses)/len(fine_losses)) #3.16
print(fine_losses)

---baseline all test set average loss---
tensor(4.1599, device='cuda:0')
[tensor(3.6336, device='cuda:0'), tensor(3.8377, device='cuda:0'), tensor(3.7180, device='cuda:0'), tensor(3.8192, device='cuda:0'), tensor(3.8119, device='cuda:0'), tensor(3.8620, device='cuda:0'), tensor(3.8672, device='cuda:0'), tensor(3.7823, device='cuda:0'), tensor(3.6336, device='cuda:0'), tensor(3.8008, device='cuda:0'), tensor(3.8584, device='cuda:0'), tensor(3.7416, device='cuda:0'), tensor(3.6316, device='cuda:0'), tensor(3.7039, device='cuda:0'), tensor(3.6806, device='cuda:0'), tensor(3.8592, device='cuda:0'), tensor(5.6584, device='cuda:0'), tensor(3.5573, device='cuda:0'), tensor(3.5560, device='cuda:0'), tensor(3.8750, device='cuda:0'), tensor(4.0477, device='cuda:0'), tensor(3.8540, device='cuda:0'), tensor(3.7438, device='cuda:0'), tensor(3.7417, device='cuda:0'), tensor(3.5581, device='cuda:0'), tensor(3.7532, device='cuda:0'), tensor(3.7034, device='cuda:0'), tensor(3.7263, device='cuda:0'), te

### target corpus (MPF)

In [ ]:
baseline_losses = []
fine_losses = []

with torch.no_grad():
    for test_batch in test_batch_generator.all_batches(batch_size = 2): #test ex n=97
        t = test_batch.to(device)
        #baseline
        outputs = model(t, labels=t)
        loss = outputs.loss
        baseline_losses.append(loss)
        #fine-tuned
        outputs = model_t(t, labels=t)
        loss = outputs.loss
        fine_losses.append(loss)

print("---baseline all test set average loss---")
print(sum(baseline_losses)/len(baseline_losses)) #4.15
print(baseline_losses)

print("---fine-tuned all test set average loss---")
print(sum(fine_losses)/len(fine_losses)) #3.16
print(fine_losses)

---baseline all test set average loss---
tensor(4.3145, device='cuda:0')
[tensor(3.8150, device='cuda:0'), tensor(7.3962, device='cuda:0'), tensor(3.6261, device='cuda:0'), tensor(3.7215, device='cuda:0'), tensor(3.5795, device='cuda:0'), tensor(4.4474, device='cuda:0'), tensor(3.3265, device='cuda:0'), tensor(3.6339, device='cuda:0'), tensor(3.6849, device='cuda:0'), tensor(3.5804, device='cuda:0'), tensor(3.5036, device='cuda:0'), tensor(3.6430, device='cuda:0'), tensor(3.4908, device='cuda:0'), tensor(3.4368, device='cuda:0'), tensor(6.1508, device='cuda:0'), tensor(3.7732, device='cuda:0'), tensor(9.0021, device='cuda:0'), tensor(3.7042, device='cuda:0'), tensor(3.6889, device='cuda:0'), tensor(3.6995, device='cuda:0'), tensor(3.7992, device='cuda:0'), tensor(7.8411, device='cuda:0'), tensor(3.9276, device='cuda:0'), tensor(11.8028, device='cuda:0'), tensor(3.2795, device='cuda:0'), tensor(3.5826, device='cuda:0'), tensor(3.4380, device='cuda:0'), tensor(3.4251, device='cuda:0'), t

In [ ]:
n = 0
for test_batch in test_batch_generator.all_batches(batch_size = 2):
    n += 1
print(n) #190 batches -> 379-380 examples

190


## perplexity
https://huggingface.co/spaces/evaluate-metric/perplexity/blob/main/README.md

In [ ]:
!pip install evaluate

from evaluate import load


Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 81.4/81.4 kB 3.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 486.2/486.2 kB 15.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 110.5/110.5 kB 17.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 212.5/212.5 kB 30.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.3/134.3 kB 20.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.0/1.0 MB 44.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 114.5/114.5 kB 19.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 268.8/268.8 kB 35.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 149.6/149.6 kB 17.4 MB/s eta 0:00:00


In [ ]:
print(path)

/content/drive/MyDrive/gpt2_train/CFPP_corpus/


### test set (CFPP)

In [ ]:
perplexity = load("perplexity", module_type="metric")

print(type(model))
#test ex n=97
lens_input = [len(t) for t in test_batch_generator.string_examples]
print(lens_input)
print(len(test_batch_generator.string_examples))
#input_texts = [t[:4000] for t in test_batch_generator.string_examples[:2]]


i = 0

baseline_per = []
fine_per = []

with torch.no_grad():
    while i < len(test_batch_generator.string_examples):
        input_texts = [t for t in test_batch_generator.string_examples[i:min(i+1, len(test_batch_generator.string_examples)+1)]]
        print(input_texts)


        #baseline
        baseline_results = perplexity.compute(predictions=input_texts,
                                            model_id='asi/gpt-fr-cased-small',
                                            add_start_token=False,
                                            batch_size=4)
                                            #device='cpu') #list of str
        print('baseline')
        #print(baseline_results)
        baseline_per.append(baseline_results['perplexities'])
        print(baseline_results['perplexities'])
        #print(baseline_results['mean_perplexity'])

        #fine-tuned
        fine_results = perplexity.compute(predictions=input_texts,
                                    model_id='/content/drive/MyDrive/gpt2_train/'+'saved_model_spk_line_break_epoch30/',
                                    add_start_token=False,
                                    batch_size=1)

        print('fine-tuned')
        #print(fine_results)
        fine_per.append(fine_results['perplexities'])
        print(fine_results['perplexities'])
        #print(fine_results['mean_perplexity'])

        print(i)
        i += 1

<class 'transformers.models.gpt2.modeling_gpt2.GPT2LMHeadModel'>
[3141, 3118, 3053, 3114, 3012, 3073, 3069, 3065, 3093, 3308, 3152, 3127, 3060, 2976, 3262, 3041, 3080, 3186, 3117, 3140, 3137, 3263, 2921, 3155, 3112, 3079, 2958, 3149, 2973, 2993, 3059, 3060, 3237, 3009, 3018, 3221, 2948, 3211, 3247, 2971, 3027, 2892, 3159, 3137, 3108, 3242, 3270, 2751, 2741, 3029, 2846, 2901, 3118, 3391, 3014, 2858, 2748, 2965, 3095, 3146, 2649, 3070, 2863, 2630, 2800, 2617, 2740, 2868, 2800, 2737, 2930, 2818, 2958, 2779, 2851, 3065, 2543, 2644, 2617, 2800, 2675, 2632, 2831, 2655, 2770, 2697, 2802, 2874, 3064, 2935, 3089, 3037, 2827, 2952, 2873, 2928, 2815, 2785, 3045, 2861, 2871, 2775, 2951, 2742, 2914, 2880, 2934, 2873, 2975, 2865, 2944, 2938, 3316, 3267, 2778, 2852, 2752, 2803, 3003, 2834, 3052, 2868, 2658, 2639, 2748, 2895, 2783, 2815, 2959, 2745, 2733, 2678, 2751, 3012, 2870, 2746, 2877, 2761, 2767, 2937, 2969, 2867, 2787, 2703, 3670, 2271, 2965, 3066, 2818, 2797, 2794, 2864, 2765, 2931, 2845, 2755

  0%|          | 0/1 [00:00<?, ?it/s]

baseline
[466.51531982421875]


  0%|          | 0/1 [00:00<?, ?it/s]

fine-tuned
[13.753935813903809]
0
["Valentine: Oui\n Sonia: Tellement le l'architecture les grands trottoires enfin je\n Valentine: Bah même\n Valentine: L'architecture est plus belle que\n Thérèse: Ah si elle est plus belle\n Valentine: Le vingtième où j'habitais vingtième c'était hlm c'était des ca- comme on dit chez nous des cages à lapin\n Thérèse: Mmh mmh\n Valentine: Que là non c'est plus c'est plus\n Valentine: Structuré\n Sonia: Ah cet immeuble\n Sonia: Est un bel\n Sonia: Immeuble\n Thérèse: Ah oui\n Valentine: Les les immeubles mais les immeubles\n Thérèse: Oui d'anciens\n Valentine: Sont beaux ici dans le douzième\n Valentine: Je trouve\n Sonia: Oui\n Valentine: Ils sont beaux oui oui moi je trouve que les immeubles du douzième sont beaux puis j'aime bien le quartier du douzième\n Thérèse: Beaucoup de commerçants il y a\n Thérèse: Tout ce qu'on veut\n Valentine: Oui on a\n Valentine: Euh\n Thérèse: Tout\n Thérèse: Au pied de de de la maison\n Sonia: Mmh mmh\n Valentine: Oui 

...

fine-tuned
[13.49044418334961]
203
["Yvette: Parce que nous allons\n Yvette: Souvent en bretagne et on se croirait à saint malo j'entends une mouette c'est pas possible c'est je dois avoir des quelque chose qui va pas dans mes oreilles et maintenant c'est très souvent on entend des mouettes hein ah oui les mouettes se développent beaucoup elles sont remontées la seine et elles sont attirées probablement par les décharges\n Sonia: Par la bien sûr\n Yvette: Et cetera et\n Yvette: Ça et ça devient un problème ça devient un problème euh je vous dis pour les les gens euh disent que les mouettes avec leur bec ou je sais pas quoi esquintent euh les toits plus que les pigeons\n Jean-Paul: D'accord\n Yvette: Donc voilà\n Sonia: Et les moineaux ça\n Yvette: Oh non\n Sonia: C'est plutôt sympa\n Yvette: Non ici alors ici euh c'est ce que j'ai trouvé difficile dans ce quartier c'est que ce qui est bien si vous voulez ce que j'ai bien aimé c'est que c'est un quartier vivant ce que j'ai pas aimé c'es

  0%|          | 0/1 [00:00<?, ?it/s]

baseline
[121.85445404052734]


  0%|          | 0/1 [00:00<?, ?it/s]

fine-tuned
[17.511716842651367]
204


In [ ]:
print("CFPP test set")
print(baseline_per)

print(fine_per)

[[466.51531982421875], [403.1903381347656], [465.16033935546875], [386.79351806640625], [396.8338317871094], [627.5051879882812], [503.61553955078125], [713.3709716796875], [480.780029296875], [426.9104919433594], [271.7025146484375], [463.1109313964844], [267.9515075683594], [563.7548828125], [532.9124145507812], [398.5629577636719], [375.28643798828125], [862.9818115234375], [541.4999389648438], [400.1234130859375], [520.6285400390625], [966.30859375], [512.7459106445312], [470.0765075683594], [383.8647155761719], [508.8136901855469], [354.5267639160156], [494.8601379394531], [352.78070068359375], [352.2942199707031], [545.126220703125], [532.46630859375], [584.033203125], [393.1031494140625], [341.2822570800781], [495.318603515625], [339.48193359375], [556.3522338867188], [789.0759887695312], [408.1897277832031], [294.33685302734375], [297.23309326171875], [370.4484558105469], [377.841552734375], [647.4215698242188], [354.2222595214844], [586.7830810546875], [172.0131072998047], [42

### target corpus (MPF)

In [ ]:
print(mpf_test_batch_generator.string_examples[2])

perplexity = load("perplexity", module_type="metric")

#test ex n=97
lens_input = [len(t) for t in mpf_test_batch_generator.string_examples]
print(lens_input)
print(len(mpf_test_batch_generator.string_examples))


i = 0

baseline_per = []
fine_per = []

with torch.no_grad():
    while i < len(mpf_test_batch_generator.string_examples):
        input_texts = [t for t in mpf_test_batch_generator.string_examples[i:min(i+1, len(mpf_test_batch_generator.string_examples)+1)]]
        print(input_texts)


        #baseline
        baseline_results = perplexity.compute(predictions=input_texts,
                                            model_id='asi/gpt-fr-cased-small',
                                            add_start_token=False,
                                            batch_size=4)
                                            #device='cpu') #list of str
        print('baseline')
        baseline_per.append(baseline_results['perplexities'])
        print(baseline_results['perplexities'])

        #fine-tuned
        fine_results = perplexity.compute(predictions=input_texts,
                                    model_id='/content/drive/MyDrive/gpt2_train/'+'saved_model_spk_line_break_epoch30/',
                                    add_start_token=False,
                                    batch_size=1)

        print('fine-tuned')
        fine_per.append(fine_results['perplexities'])
        print(fine_results['perplexities'])

        print(i)
        i += 1



Baligh: Ouais
 Lucile: Celle avec qui je parle de fringues et tout c'est jessica
 Baligh: D'accord
 Lucile: Voilà
 Baligh: D'accord d'accord d'accord et euh ça se passe bien entre vous tu as pas été victime de rumeurs par exemple ou euh euh initiatrice de rumeurs pour casser des gens ou quoi que ce soit je sais pas ?
 Lucile: Alors moi je je casse souvent les gens mais c'est toujours gentil
 Baligh: Ouais
 Baligh: Vous vous charriez beaucoup ?
 Lucile: Et euh
 Lucile: Ouais mais c'est c'est c'est le but c'est marrant ça nous fait rigoler c'est jamais euh c'est c'est jamais péjoratif ce qu'on dit les uns sur les les uns sur les autres sauf si on s'aime pas et euh
 Baligh: Donc il il il faut se connaître en fait pour euh pour se charrier quoi
 Lucile: Quelque part euh
 Lucile: Ben moi ouais moi si bien sûr il y a eu des rumeurs même des des très bons amis euh qui qui me disent ouais euh je à l'apparence ouais ça y est tu es pétée de thunes alors que genre je me ra- je me ramène à l'école

[2821, 2786, 2611, 2780, 2534, 2714, 2782, 100, 2863, 2746, 2895, 2899, 3024, 1538, 2934, 2839, 2864, 3063, 2938, 2890, 3042, 2818, 2919, 3133, 2951, 2967, 2875, 2939, 2997, 2824, 2905, 2962, 3014, 2370, 2835, 2852, 2773, 2933, 2748, 2689, 2679, 2869, 2697, 2758, 2768, 2807, 2876, 2943, 2836, 1755, 2990, 2716, 2732, 2942, 2965, 2640, 2643, 2538, 2613, 2629, 2823, 2746, 2615, 2679, 2654, 2770, 2651, 2772, 2555, 2669, 2696, 2576, 2666, 2747, 2679, 2731, 2666, 2658, 2757, 2581, 1415, 2651, 2785, 2714, 2726, 2731, 2867, 2736, 2890, 2819, 2811, 2790, 2744, 2673, 2822, 2652, 2984, 2779, 2809, 2669, 2788, 3024, 2909, 2840, 2770, 2539, 2578, 2868, 2909, 2816, 2718, 2679, 2854, 2627, 2796, 2761, 1873, 2919, 2756, 2761, 2836, 2883, 1779, 2811, 2824, 2684, 2644, 2679, 3305, 2880, 2802, 3165, 2949, 2867, 2840, 2770, 3030, 2603, 2712, 2761, 2901, 2894, 2955, 2874, 2922, 3085, 2889, 2705, 2771, 2802, 2739, 2838, 2984, 2790, 2861, 1849, 2832, 2957, 2805, 2759, 2772, 3023, 2828, 2909, 2915, 2924, 2783

  0%|          | 0/1 [00:00<?, ?it/s]

baseline
[138.67959594726562]


  0%|          | 0/1 [00:00<?, ?it/s]

...

baseline
[229.25392150878906]


  0%|          | 0/1 [00:00<?, ?it/s]

fine-tuned
[21.243003845214844]
169
["Hassan: Elles foutent le darwa\n Bélinda: S'enjailler c'est ce que font les niafou\n Bélinda: Genre\n Bélinda: Hé hé ouais xxx elles font de la musique elles dansent et tout\n Lidia: Elles dansent\n Lidia: Avec xx elles font de la musique\n Joanne: D'accord s'amuser quoi\n Joanne: Non?\n Bélinda: Xxx\n Joanne: Un petit peu ?\n Bélinda: Non\n Joanne: D'accord\n Joanne: Et un fatou une fatou ?\n Bélinda: C'est une niafou\n Joanne: Ah c'est non mais c'est pas elle\n Bélinda: Xxx va\n Joanne: O k\n Hassan: Hé j'ai mangé cet après-midi\n Joanne: Euh avoir du flow qu'est-ce que c'est avoir du flow oui ?\n Lidia: Avoir du flow@s?\n Bélinda: Avoir du style\n Hassan: Xxx\n Joanne: Du style ?\n Hassan: Xx\n Hassan: Un peu x\n Joanne: Ah d'accord c'est comme ouais le swag quoi non xx c'est ça ?\n Bélinda: Ouais\n Hassan: Xx\n Joanne: O k\n Bélinda: Mais en fait maintenant le swag euh\n Joanne: Oh vous l'utilisez plus c'est ça ?\n Bélinda: Non plus trop\n Joan

  0%|          | 0/1 [00:00<?, ?it/s]

RuntimeError: ignored